In [1]:
import geopandas as gpd
import pandas as pd

In [2]:
blds=gpd.read_file('BASEMAP_Buildings/BASEMAP_Buildings.shp')

# Get buildings inside a buffer around Volpe

In [4]:
volpe_buffer=gpd.read_file('rough_kendall.geojson')
blds['copy_id']=blds.index.copy()
blds_ids_in_buffer=gpd.overlay(
    blds.to_crs(volpe_buffer.crs), volpe_buffer)['copy_id'].unique()
blds=blds.loc[blds_ids_in_buffer]

In [5]:
blds.geometry=blds.geometry.scale(
    xfact=1.0, yfact=1.0, zfact=0.0001, origin=[0,0,0])

In [6]:
lu=gpd.read_file('CDD_LandUse/CDD_LandUse.shp')

In [7]:
lu['Category'].unique()

array(['Residential', 'Vacant Residential', 'Public Open Space', 'Office',
       'Commercial', 'Mixed Use Residential', 'Transportation', 'Health',
       'Utility', 'Vacant Commercial', 'Mixed Use Commercial',
       'Assisted Living/Boarding House', 'Industrial', 'Higher Education',
       'Charitable/Religious', 'Education', 'Education Residential',
       'Vacant Industrial', 'Office/R&D', 'Cemetery',
       'Government Operations', 'Privately-Owned Open Space',
       'Mixed Use Education'], dtype=object)

In [8]:
vacant_commercial=lu.loc[lu['Category']=='Vacant Commercial'].copy()
vacant_commercial.explore(tooltip=None)

In [9]:
vacant_commercial['area']=vacant_commercial.geometry.area*0.093
vacant_commercial=vacant_commercial.to_crs('epsg:4326')
vacant_commercial.to_file('vacant_commercial.geojson')

In [10]:
vacant_residential=lu.loc[lu['Category']=='Vacant Residential'].copy()
vacant_residential.explore()

In [11]:
vacant_residential['area']=vacant_residential.geometry.area*0.093
vacant_residential=vacant_residential.to_crs('epsg:4326')
vacant_residential.to_file('vacant_residential.geojson')

In [12]:
open_space=lu.loc[lu['Category'].isin(
    ['Public Open Space', 'Privately-Owned Open Space'])].copy()

In [13]:
open_space.explore(column='Category', legend=True, tiles='CartoDB Positron')

In [14]:
lu=lu.loc[~(lu['Category'].isin(
    ['Public Open Space', 'Privately-Owned Open Space']))].copy()

# Overlay buildings with LU

In [15]:
blds=blds.loc[blds['TYPE']=='BLDG']

In [16]:
blds_lu=blds.overlay(lu.to_crs(blds.crs), 'intersection')

In [17]:
blds_lu.explore(column='Category', legend=True, tiles='CartoDB Positron')

In [18]:
blds_lu['bld_height[ft]']=blds_lu['ELEV_SL']-blds_lu['BASE_ELEV']
blds_lu['bld_height[ft]'].describe()

count    275.000000
mean      83.433455
std       66.887593
min       -9.800000
25%       29.000000
50%       65.700000
75%      118.550000
max      270.200000
Name: bld_height[ft], dtype: float64

In [19]:
blds_lu['floors']=(blds_lu['bld_height[ft]']/13).round()

In [20]:
blds_lu.loc[blds_lu['floors']<1, 'floors']=1

# Overlay with Demographic data
- using outputs of Cityscope/Tables/kendall/volpe_geom_data.ipynb
## Method:
- Get buildings which overlap with local block groups
- Calculate their floor areas
- Assign every building to one block group
- For every block group:
    - assign the employment to office and commercial
    - assign the residents to residential
    - assign study to educational
    - assign student residents to resi education

In [22]:
bgs_local=gpd.read_file('bgs_local.geojson')

In [23]:
blds_lu_over_bgs_local=gpd.overlay(blds_lu.to_crs(bgs_local.crs), bgs_local)

bld_ids_overlap= blds_lu_over_bgs_local['BldgID'].unique()
bg_ids_overlap=blds_lu_over_bgs_local['GEOID'].unique()

In [24]:
blds_lu_local=blds_lu.loc[blds_lu['BldgID'].isin(bld_ids_overlap)].copy()

In [25]:
blds_lu_local['area [m2]']=blds_lu_local.geometry.area*0.093

In [26]:
blds_lu_local['total_floor_area']=(blds_lu_local['area [m2]']*
                                   blds_lu_local['floors'])

In [27]:
blds_lu_local['Resi_m2']=(blds_lu_local['total_floor_area']*
                          blds_lu_local['Category'].str.contains('Residential|House'))
blds_lu_local['Emp_m2']=(blds_lu_local['total_floor_area']*
                          blds_lu_local['Category'].str.contains('Office|Commercial|Industrial|Health'))
blds_lu_local['Edu_m2']=(blds_lu_local['total_floor_area']*
                          blds_lu_local['Category'].isin(['Higher Education', 'Education', 'Mixed Use Education']))

Convert to Point geometry to assign each to one BG 

In [28]:
blds_lu_local=blds_lu_local.rename(columns={'geometry': 'poly_geom'})
blds_lu_local.geometry=blds_lu_local['poly_geom'].centroid

In [29]:
blds_points_over_bgs_local=gpd.overlay(
    blds_lu_local.to_crs(bgs_local.crs), bgs_local, keep_geom_type=False)

In [30]:
floor_area_by_bg_cat=blds_points_over_bgs_local.groupby('GEOID')[
    ['Resi_m2', 'Emp_m2', 'Edu_m2']].sum()
floor_area_by_bg_cat=floor_area_by_bg_cat.rename(
    columns={col: col+'_total_bg' for col in floor_area_by_bg_cat.columns})
floor_area_by_bg_cat.head()

Resi_m2_total_bg  Emp_m2_total_bg  Edu_m2_total_bg
GEOID                                                           
250173523001      56455.112732    257592.822115         0.000000
250173523002     141738.651351    478088.459617         0.000000
250173524001          0.000000    236570.148552         0.000000
250173524002      22957.427764    914683.692892     24239.755382
250173526001          0.000000     20068.534523         0.000000

In [31]:
blds_points_over_bgs_local=blds_points_over_bgs_local.merge(
    floor_area_by_bg_cat, left_on='GEOID', right_index=True)

In [32]:
for col in ['resi_income_low','resi_income_mid','resi_income_high','res_total', 'resi_students']:
    blds_points_over_bgs_local['bld_'+col]=(blds_points_over_bgs_local[col]*
                                       (blds_points_over_bgs_local['Resi_m2']/
                                        blds_points_over_bgs_local['Resi_m2_total_bg']))
    
for col in ['work_income_low','work_income_mid','work_income_high','emp_total']:
    blds_points_over_bgs_local['bld_'+col]=(blds_points_over_bgs_local[col]*
                                       (blds_points_over_bgs_local['Emp_m2']/
                                        blds_points_over_bgs_local['Emp_m2_total_bg']))
    
for col in ['study']:
    blds_points_over_bgs_local['bld_'+col]=(blds_points_over_bgs_local[col]*
                                       (blds_points_over_bgs_local['Edu_m2']/
                                        blds_points_over_bgs_local['Edu_m2_total_bg']))

In [33]:
blds_local=blds_points_over_bgs_local[[
    'bld_height[ft]', 'floors','total_floor_area',
    'bld_resi_income_low', 'bld_resi_income_mid', 
    'bld_resi_income_high','bld_res_total', 'bld_resi_students', 
    'bld_work_income_low','bld_work_income_mid', 'bld_work_income_high', 
    'bld_emp_total','bld_study', 'geometry', 'poly_geom']]

In [34]:
blds_local['geometry']=blds_local['poly_geom']
blds_local.geometry=blds_local['poly_geom']

/opt/anaconda3/envs/geo/lib/python3.9/site-packages/geopandas/geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [35]:
blds_local=blds_local.to_crs('epsg:4326')

In [36]:
blds_local.explore(column='bld_resi_students')

In [37]:
bgs_local.loc[bgs_local['GEOID'].isin(bg_ids_overlap)].sum()

/var/folders/30/clhynt5s7fx_3nyyxfl04f780000gn/T/ipykernel_35445/2344865378.py:1: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  bgs_local.loc[bgs_local['GEOID'].isin(bg_ids_overlap)].sum()


index                                                   1501041151029
GEOID               2501735260012501735240022501735230012501735240...
resi_students                                                  1033.0
study                                                          1444.0
work_income_low                                               11871.0
work_income_mid                                               17761.0
work_income_high                                              20201.0
resi_income_low                                                1495.0
resi_income_mid                                                2295.0
resi_income_high                                               2078.0
res_total                                                      6901.0
emp_total                                                     49833.0
dtype: object

Num students studying in the area is too low- double the number of students in each building

In [38]:
blds_local['bld_study']*=2

In [39]:
local_bounds=bgs_local.total_bounds

In [40]:
open_space['open_space_area [m2]']=open_space.geometry.area*0.093
open_space_local=open_space.to_crs(bgs_local.crs).cx[
    local_bounds[0]:local_bounds[2], local_bounds[1]:local_bounds[3]]

In [41]:
open_space_local.explore()

In [42]:
all_spaces=pd.concat([blds_local.rename(columns={col: col.replace('bld_', '') for col in blds_local.columns}),
                      bgs_local.loc[~(bgs_local['GEOID'].isin(bg_ids_overlap))],
                      open_space_local[['open_space_area [m2]', 'geometry']]])

In [43]:
all_spaces.explore(column='emp_total')

In [44]:
all_spaces.explore(column='open_space_area [m2]')

In [45]:
all_spaces[[col for col in all_spaces.columns if not col=='poly_geom'
           ]].to_file('all_spaces2.geojson')

In [46]:
len(all_spaces)

473